In [ ]:
# !pip install --upgrade pm4py

In [ ]:
import pm4py
from pm4py.algo.conformance.tokenreplay import algorithm as token_replay
from pm4py.objects.petri_net.importer import importer as petri_importer  
from pm4py.visualization.petri_net import visualizer as petri_visualizer  
import pandas as pd
import os
import json
def load_pnml_model(pnml_file_path):
    net, initial_marking, final_marking = petri_importer.apply(pnml_file_path)
    return net, initial_marking, final_marking

def load_csv_log(csv_file_path):
    df = pd.read_csv(csv_file_path)
    log = pm4py.format_dataframe(df, timestamp_key="time:timestamp")
    return log, df

def apply_token_replay(log, net, initial_marking, final_marking):
    replayed_traces = token_replay.apply(log, net, initial_marking, final_marking)
    return replayed_traces


def check_for_anomalies(replayed_traces, df):
    case_names = df['case:concept:name'].unique()
    compliant_cases = []
    non_compliant_cases = []
    
    for i, trace_result in enumerate(replayed_traces):
        current_case_name = case_names[i]
        case_data = df[df['case:concept:name'] == current_case_name]
        
        if not trace_result['trace_is_fit']:
            print(f"Anomaly detected in case '{current_case_name}'.")
            non_compliant_cases.append(case_data)
        else:
            print(f"Case '{current_case_name}' is compliant.")
            compliant_cases.append(case_data)
    
    return compliant_cases, non_compliant_cases

def calculate_compliance_percentage(replayed_traces):
    total_cases = len(replayed_traces)
    compliant_cases = sum([1 for trace_result in replayed_traces if trace_result['trace_is_fit']])
    non_compliant_cases = total_cases - compliant_cases

    compliant_percentage = (compliant_cases / total_cases) * 100
    non_compliant_percentage = (non_compliant_cases / total_cases) * 100

    print(f"Total cases: {total_cases}")
    print(f"Compliant cases: {compliant_cases} ({compliant_percentage:.2f}%)")
    print(f"Non-compliant cases: {non_compliant_cases} ({non_compliant_percentage:.2f}%)")

    return {
        "total_cases": total_cases,
        "compliant_cases": compliant_cases,
        "non_compliant_cases": non_compliant_cases,
        "compliant_percentage": compliant_percentage,
        "non_compliant_percentage": non_compliant_percentage,
    }

def save_pnml_model_as_png(net, initial_marking, final_marking, png_output_path):
    gviz = petri_visualizer.apply(net, initial_marking, final_marking)
    petri_visualizer.save(gviz,"data/"+png_output_path +".png")
    print(f"Petri Net model saved as PNG at: {png_output_path}.png")


def save_results_to_csv(compliant_cases, non_compliant_cases, output_file_path):
    compliant_df = pd.concat(compliant_cases)
    non_compliant_df = pd.concat(non_compliant_cases)

    # ذخیره به فایل CSV
    compliant_df.to_csv("data/compliant_"+output_file_path + ".csv", index=False)
    non_compliant_df.to_csv("data/non_compliant_"+output_file_path + ".csv", index=False)

    print(f"Compliant cases saved to {output_file_path}_compliant.csv")
    print(f"Non-compliant cases saved to {output_file_path}_non_compliant.csv")


def process_log(pnml_file_path, csv_file_path):

    pnml_file_name = os.path.splitext(os.path.basename(pnml_file_path))[0]
    csv_file_name = os.path.splitext(os.path.basename(csv_file_path))[0]
    output_file_base_name = f"{pnml_file_name}_{csv_file_name}"

    net, initial_marking, final_marking = load_pnml_model(pnml_file_path)
    
    log, df = load_csv_log(csv_file_path)
    
    replayed_traces = apply_token_replay(log, net, initial_marking, final_marking)
    
    compliant_cases, non_compliant_cases = check_for_anomalies(replayed_traces, df)
    
    stats = calculate_compliance_percentage(replayed_traces)
    
    summary = {
        "model_file": os.path.basename(pnml_file_path),
        "log_file": os.path.basename(csv_file_path),
        "stats": stats
    }

    summary_file_path = "data/"+output_file_base_name + "_summary.json"
    with open(summary_file_path, "w", encoding="utf-8") as f:
        json.dump(summary, f, indent=4, ensure_ascii=False)

    print(f"Summary saved to {summary_file_path}")

    save_results_to_csv(compliant_cases, non_compliant_cases, output_file_base_name)
    
    save_pnml_model_as_png(net, initial_marking, final_marking, output_file_base_name)


In [48]:
pnml_file_path = "./data/heuristic_SP_DF_cleaned.pnml"  
log_csv_file_path = "./data/SP_DF_cleaned.csv"  
process_log(pnml_file_path, log_csv_file_path)

replaying log with TBR, completed traces :: 100%|██████████| 1028/1028 [00:02<00:00, 469.13it/s]


Case '1' is compliant.
Anomaly detected in case '2'.
Case '3' is compliant.
Anomaly detected in case '4'.
Case '5' is compliant.
Case '6' is compliant.
Anomaly detected in case '7'.
Case '8' is compliant.
Anomaly detected in case '9'.
Case '10' is compliant.
Case '11' is compliant.
Case '12' is compliant.
Anomaly detected in case '13'.
Anomaly detected in case '14'.
Anomaly detected in case '15'.
Case '16' is compliant.
Anomaly detected in case '17'.
Case '18' is compliant.
Anomaly detected in case '19'.
Anomaly detected in case '20'.
Case '21' is compliant.
Case '22' is compliant.
Anomaly detected in case '23'.
Anomaly detected in case '24'.
Case '25' is compliant.
Anomaly detected in case '26'.
Anomaly detected in case '27'.
Anomaly detected in case '28'.
Anomaly detected in case '29'.
Case '30' is compliant.
Case '31' is compliant.
Case '32' is compliant.
Case '33' is compliant.
Anomaly detected in case '34'.
Case '35' is compliant.
Case '36' is compliant.
Anomaly detected in case '

In [49]:
pnml_file_path = "./data/alpha_SP_DF_cleaned.pnml"  
log_csv_file_path = "./data/SP_DF_cleaned.csv"  

process_log(pnml_file_path, log_csv_file_path)

replaying log with TBR, completed traces :: 100%|██████████| 1028/1028 [00:02<00:00, 467.12it/s]


Anomaly detected in case '1'.
Anomaly detected in case '2'.
Anomaly detected in case '3'.
Anomaly detected in case '4'.
Anomaly detected in case '5'.
Anomaly detected in case '6'.
Anomaly detected in case '7'.
Case '8' is compliant.
Anomaly detected in case '9'.
Case '10' is compliant.
Anomaly detected in case '11'.
Case '12' is compliant.
Anomaly detected in case '13'.
Anomaly detected in case '14'.
Anomaly detected in case '15'.
Case '16' is compliant.
Anomaly detected in case '17'.
Anomaly detected in case '18'.
Anomaly detected in case '19'.
Anomaly detected in case '20'.
Case '21' is compliant.
Anomaly detected in case '22'.
Anomaly detected in case '23'.
Anomaly detected in case '24'.
Case '25' is compliant.
Anomaly detected in case '26'.
Anomaly detected in case '27'.
Anomaly detected in case '28'.
Anomaly detected in case '29'.
Case '30' is compliant.
Case '31' is compliant.
Anomaly detected in case '32'.
Anomaly detected in case '33'.
Anomaly detected in case '34'.
Anomaly det